<a href="https://colab.research.google.com/github/Untick/InspectrumClinic_RS_gr1/blob/main/Marfida%20Alexander/a_marfida_2023_05_22.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Стажировка. Профпатолог (INSPECTRUM CLINIC) 

## Исследование датасета

In [ ]:
# Подключение библиотек
import gdown
import numpy as np
import matplotlib.pyplot as plt
plt.style.use('dark_background')
import seaborn as sns
from fastai.tabular import *
import pandas as pd


### Загрузка и запись данных

#### Загрузка файла из облака в colab

In [ ]:
import gdown

# gdown.download('https://storage.yandexcloud.net/aiueducation/Content/base/l9/wine_base.csv', None, quiet=True)
gdown.download('https://storage.yandexcloud.net/terratraineeship/23_InspectrumClinic_RS/datasets/%D0%B4%D0%B0%D1%82%D0%B0%D1%81%D0%B5%D1%82%20%D0%BF%D1%80%D0%BE%D1%84%D0%BF%D0%B0%D1%82%D0%BE%D0%BB%D0%BE%D0%B3%20%D1%87%D0%B0%D1%81%D1%82%D1%8C.xlsx', None, quiet=True)


'%D0%B4%D0%B0%D1%82%D0%B0%D1%81%D0%B5%D1%82%20%D0%BF%D1%80%D0%BE%D1%84%D0%BF%D0%B0%D1%82%D0%BE%D0%BB%D0%BE%D0%B3%20%D1%87%D0%B0%D1%81%D1%82%D1%8C.xlsx'

Файл переименован в **ICdata.xlsx**

#### Монтирование к ВМ Goole Drive
и копирование датасета

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
# Чтение исходного фрейма, от заказчика
# df_backup = pd.read_excel('ICdata.xlsx')
df_backup = pd.read_excel('/content/drive/MyDrive/УИИ(marphida)/Стажировка Профпатолог/ICdata.xlsx')

### Создание копии датасета в рабочей переменной и/или в MyDrive

In [ ]:
# df.to_excel('/content/drive/MyDrive/УИИ(marphida)/Стажировка Профпатолог/ICtest.xlsx')
#df_backup.to_excel('/content/drive/MyDrive/УИИ(marphida)/Стажировка Профпатолог/ICtest.xlsx', index=False)#, encoding='utf-8-sig')
    #!# /usr/local/lib/python3.10/dist-packages/pandas/util/_decorators.py:211: FutureWarning: the 'encoding' keyword is deprecated and will be removed in a future version. Please take steps to stop the use of 'encoding'
    #!# return func(*args, **kwargs)
df_backup = pd.read_excel('/content/drive/MyDrive/УИИ(marphida)/Стажировка Профпатолог/ICtest.xlsx')

In [ ]:
df = df_backup.copy(deep=True)
# df = df_backup.copy()

 ### Анализ и предобработка данных:

In [ ]:
# Исходный размер датафрейма
df.shape

(1982, 4587)

In [ ]:
# Удаление дублируемых строк
df.drop_duplicates(inplace=True)

In [ ]:
# Размер данных после удаления дублируемых строк
df.shape

(1926, 4587)

In [ ]:
1982 - 1926

56

Удалено 56 дублируемых строк

Проверка наличия пустых столбцов и их удаление:

In [ ]:
dn = df.isnull().sum()
print('Количество пустых столбцов:', len(dn[dn == 1926]))
df.dropna(axis=1, how='all', inplace=True)
df.shape

Количество пустых столбцов: 884


(1926, 3703)

In [ ]:
df.info(memory_usage='deep')

<class 'pandas.core.frame.DataFrame'>
Int64Index: 1926 entries, 0 to 1981
Columns: 3703 entries, ДокументПрохождениеМедосмотра to Офтальмология1_ДвигательныйАппаратГлазДополнение_ЗначениеПредставление
dtypes: bool(1), datetime64[ns](43), float64(453), object(3206)
memory usage: 250.9 MB


In [ ]:
# Просмотр содержания ненулевых значений полей в выбранных колонках
for colname in [
 'ЗаключениеМК',
 'ЗаключениеМКПредставление',
 'Заключение'
     ]:
  print(df.loc[~df[colname].isnull(), colname])

0                        Годен
1                        Годен
2       ГоденСКоррекциейЗрения
3                        Годен
4       ГоденСКоррекциейЗрения
                 ...          
1961                     Годен
1962                     Годен
1972                     Годен
1973                     Годен
1981                     Годен
Name: ЗаключениеМК, Length: 1519, dtype: object
0                     Годен к работе в указанных условиях
1                     Годен к работе в указанных условиях
2       Годен к работе в указанных условиях (с коррекц...
3                     Годен к работе в указанных условиях
4       Годен к работе в указанных условиях (с коррекц...
                              ...                        
1961                  Годен к работе в указанных условиях
1962                  Годен к работе в указанных условиях
1972                  Годен к работе в указанных условиях
1973                  Годен к работе в указанных условиях
1981                  Годен к р

In [ ]:
# Формирование списка сохраняемых столбцов
# dfcols_to_save.append(df.columns[df.columns.str.contains('Обследование')].to_numpy())
dfcols_to_save = ['КлиентДатаРождения', 'КлиентПолПредставление', 'Профессия',
                  'ЗаключениеМК',
                  'ЗаключениеМКПредставление',
                  'ВредныеФакторы']
dfcols_to_save = dfcols_to_save + list(df.columns[df.columns.str.contains('Обследование')].to_numpy())
dfcols_to_save = dfcols_to_save + list(df.columns[df.columns.str.contains('Заключение_ЗначениеПредставление')].to_numpy())
dfcols_to_save = dfcols_to_save + list(df.columns[df.columns.str.contains('ГоденНегоден_ЗначениеПредставление')].to_numpy())
dfcols_to_save = dfcols_to_save + list(df.columns[df.columns.str.contains('Диагноз_ЗначениеПредставление')].to_numpy())
dfcols_to_save = dfcols_to_save + list(df.columns[df.columns.str.contains('ПрофнепригодностьВременнаяПредставление1')].to_numpy())
dfcols_to_save = dfcols_to_save + list(df.columns[df.columns.str.contains('ПрофнепригодностьВременнаяПредставление2')].to_numpy())
dfcols_to_save = dfcols_to_save + list(df.columns[df.columns.str.contains('МКБ101')].to_numpy())

dfcols_to_save

['КлиентДатаРождения',
 'КлиентПолПредставление',
 'Профессия',
 'ЗаключениеМК',
 'ЗаключениеМКПредставление',
 'ВредныеФакторы',
 'ФункциональнаяДиагностика1_ОбследованиеПроведено_Значение',
 'ФункциональнаяДиагностика1_ОбследованиеПроведено_ЗначениеПредставление',
 'Дерматовенерология1_ОбследованиеНаПедикулез_Значение',
 'Дерматовенерология1_ОбследованиеНаПедикулез_ЗначениеПредставление',
 'ЭКГНеИсп1_ОбследованиеПроведено_Значение',
 'ЭКГНеИсп1_ОбследованиеПроведено_ЗначениеПредставление',
 'Хирургия1_ОбследованиеНаПедикулез_Значение',
 'Хирургия1_ОбследованиеНаПедикулез_ЗначениеПредставление',
 'ФункциональнаяДиагностика2_ОбследованиеПроведено_Значение',
 'ФункциональнаяДиагностика2_ОбследованиеПроведено_ЗначениеПредставление',
 'Дерматовенерология2_ОбследованиеНаПедикулез_Значение',
 'Дерматовенерология2_ОбследованиеНаПедикулез_ЗначениеПредставление',
 'Хирургия3_ОбследованиеНаПедикулез_Значение',
 'Хирургия3_ОбследованиеНаПедикулез_ЗначениеПредставление',
 'Хирургия2_ОбследованиеН

In [ ]:
# Удаление из датафрейма всех не выбранных для сохранения колонок
i = 0
try:
  while True:
    for col_to_save in dfcols_to_save:
      if df.columns[i] == col_to_save:
        i += 1
        continue
    else:
      df.drop(df.columns[i], axis= 1 , inplace=True)
except IndexError:
  df.shape

In [ ]:
df.shape
#dfcols
#df

(1926, 77)

In [ ]:
# Наименования всех оставшихся колонок
df.columns.to_list()

['КлиентДатаРождения',
 'КлиентПолПредставление',
 'Профессия',
 'ЗаключениеМК',
 'ЗаключениеМКПредставление',
 'Заключение',
 'ВредныеФакторы',
 'Рентгенология1_Заключение_ЗначениеПредставление',
 'ПсихиатрияНаркология1_МКБ101',
 'ПсихиатрияНаркология1_ПрофнепригодностьВременнаяПредставление1',
 'ПсихиатрияНаркология1_ГоденНегоден_ЗначениеПредставление',
 'ПсихиатрияНаркология1_Диагноз_ЗначениеПредставление',
 'Офтальмология1_МКБ101',
 'Офтальмология1_ПрофнепригодностьВременнаяПредставление1',
 'Офтальмология1_ГоденНегоден_ЗначениеПредставление',
 'Офтальмология1_Диагноз_ЗначениеПредставление',
 'Оториноларингология1_МКБ101',
 'Оториноларингология1_ПрофнепригодностьВременнаяПредставление1',
 'Оториноларингология1_ГоденНегоден_ЗначениеПредставление',
 'Оториноларингология1_Диагноз_ЗначениеПредставление',
 'ХирургНеИсп1_МКБ101',
 'ХирургНеИсп1_ПрофнепригодностьВременнаяПредставление1',
 'ХирургНеИсп1_ГоденНегоден_ЗначениеПредставление',
 'ХирургНеИсп1_Диагноз_ЗначениеПредставление',
 'Г

In [ ]:
df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 1926 entries, 0 to 1981
Data columns (total 77 columns):
 #   Column                                                                  Non-Null Count  Dtype         
---  ------                                                                  --------------  -----         
 0   КлиентДатаРождения                                                      1926 non-null   datetime64[ns]
 1   КлиентПолПредставление                                                  1926 non-null   object        
 2   Профессия                                                               1926 non-null   object        
 3   ЗаключениеМК                                                            1519 non-null   object        
 4   ЗаключениеМКПредставление                                               1519 non-null   object        
 5   Заключение                                                              1507 non-null   object        
 6   ВредныеФакторы          

In [ ]:
# df_backup.select_dtypes(include=['float64']).columns

In [ ]:
df = df.fillna('Не определено')

In [ ]:
# ohee - структура тестироваия всех преобразований столбцов в ohe
#ohee = [{},{}]
ohee = dict()
for col_name in df.select_dtypes(include=['object']).columns:
  uniq_elem = df[col_name].unique()
  uni_count = len(uniq_elem)
  col_ohe = {}
  i = 0
#  was_nan = False
  for el in uniq_elem:
#    # print('"'+f'{el}'+'"')
#    if el == np.nan:
#      el = 'не определено'
#      was_nan = True
    col_ohe[f'{el}'] = np.zeros((uni_count))
    col_ohe[f'{el}'][i] = 1
    i += 1
#  if was_nan == False:
#    col_ohe['не определено'] = np.zeros((uni_count))
#    col_ohe['не определено'][i] = 1
  ohee.update([(f'{col_name}',col_ohe)])

In [ ]:
ohee

{'КлиентПолПредставление': {'Женский': array([1., 0.]),
  'Мужской': array([0., 1.])},
 'Профессия': {'Ведущий специалист по организации обуения': array([1., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
         0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
         0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
         0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
         0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
         0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
         0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
         0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
         0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
         0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
         0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
        